<a href="https://colab.research.google.com/github/MarioCastilloM/AlgoTrading/blob/main/AlgoTrading.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# AlgoTrading Python

## Libraries

In [ ]:
!pip install ta
import matplotlib.pyplot as plt
import numpy as np
from sklearn.datasets import load_digits
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
import pandas_datareader as pdr
from ta import add_all_ta_features
from ta.utils import dropna

  Created wheel for ta: filename=ta-0.7.0-py3-none-any.whl size=28716 sha256=8fc24b43a25a1c52edfa64afe4fd79479e334d888ed4f715f6074e5265d3ceff
  Stored in directory: /root/.cache/pip/wheels/5e/74/e0/72395003bd1d3c8f3f5860c2d180ff15699e47a2733d8ebd38
Successfully built ta


## Data from Tiingo (pandas-datareader)

In [ ]:
tickers = ['btcusd', 'ethusd', 'eosusd']

In [ ]:
crypto=pdr.get_data_tiingo(tickers, api_key = 'e03221a264e57841f1ff73d92bfcaff7008c4291')

In [ ]:
crypto.reset_index(inplace=True)
crypto.head()

symbol                      date   close  ...    adjVolume  divCash  splitFactor
0  btcusd 2016-08-14 00:00:00+00:00  583.52  ...  2032.613346      0.0          1.0
1  btcusd 2016-08-15 00:00:00+00:00  568.76  ...  5567.695302      0.0          1.0
2  btcusd 2016-08-16 00:00:00+00:00  565.55  ...  5256.919773      0.0          1.0
3  btcusd 2016-08-17 00:00:00+00:00  574.99  ...  5303.470655      0.0          1.0
4  btcusd 2016-08-18 00:00:00+00:00  570.91  ...  4528.424150      0.0          1.0

[5 rows x 14 columns]

In [ ]:
btc = crypto[crypto['symbol']=='btcusd']

## All Features with TA library

In [ ]:
btc_ft = add_all_ta_features(btc[['date', 'open', 'high', 'low', 'close', 'volume']], open="open", high="high", low="low", close="close", volume="volume", fillna=True)

/usr/local/lib/python3.7/dist-packages/ta/wrapper.py:90: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  high=df[high], low=df[low], close=df[close], volume=df[volume], fillna=fillna
/usr/local/lib/python3.7/dist-packages/ta/wrapper.py:95: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  close=df[close], volume=df[volume], fillna=fillna
/usr/local/lib/python3.7/dist-packages/ta/wrapper.py:100: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,c

In [ ]:
btc_ft

date          open  ...  others_dlr    others_cr
0    2016-08-14 00:00:00+00:00    585.613826  ...    0.000000     0.000000
1    2016-08-15 00:00:00+00:00    567.990917  ...   -2.562017    -2.529476
2    2016-08-16 00:00:00+00:00    563.722206  ...   -0.565984    -3.079586
3    2016-08-17 00:00:00+00:00    576.520235  ...    1.655394    -1.461818
4    2016-08-18 00:00:00+00:00    572.289005  ...   -0.712107    -2.161023
...                        ...           ...  ...         ...          ...
1820 2021-08-08 00:00:00+00:00  44521.615475  ...   -1.873313  7406.550733
1821 2021-08-09 00:00:00+00:00  43801.683990  ...    5.469052  7828.521665
1822 2021-08-10 00:00:00+00:00  46259.066831  ...   -1.468772  7712.920811
1823 2021-08-11 00:00:00+00:00  45586.820203  ...   -0.154332  7700.872295
1824 2021-08-12 00:00:00+00:00  45525.750991  ...   -2.721621  7491.425193

[1825 rows x 89 columns]

In [ ]:
import plotly.express as px

fig = px.line(btc_ft, x = btc_ft['date'], y = btc_ft.iloc[:,1], title = 'Technical Analysis')
for col in btc_ft.columns[2:]:
  if 'volume' not in col and 'volatility' not in col and 'momentum' not in col and 'others' not in col:
    fig.add_scatter(x = btc_ft['date'], y = btc_ft[col], name = col)
fig.show()

## Step by step Technical Analysis

### MACD, Signal Line and Exponential Moving Average

In [ ]:
def ema(ts, days, smooth):
  ts = np.array(ts)
  ma = np.zeros(len(ts))
  ma[0] = ts[0]
  for i in range(1, len(ts)):
    ma[i] = ts[i]*(smooth/(1+days)) + ma[i-1]*(1-(smooth/(1+days)))
  return ma

In [ ]:
ema_btc = ema(btc.close, 26, 2)
ema_btc_12 = ema(btc.close, 12, 2)
MACD = ema_btc - ema_btc_12
signal = ema(MACD, 9, 2)
histogram = MACD-signal

In [ ]:
import plotly.subplots as sp

# Create figures in Express
figure1 = px.line(btc_ft, x = 'date', y = 'close', title = 'BTC MACD vs Signal Line')

fig = px.line(x = btc.date, y = MACD,
              labels={
                     "x": "Date",
                     "y": ""
                     })

fig = fig.add_scatter(x = btc.date, y = signal, name = 'Signal')
fig = fig.add_bar(x = btc.date, y = histogram, name = 'Histograma')

figure2 = fig

# For as many traces that exist per Express figure, get the traces from each plot and store them in an array.
# This is essentially breaking down the Express fig into it's traces
figure1_traces = []
figure2_traces = []
for trace in range(len(figure1["data"])):
    figure1_traces.append(figure1["data"][trace])
for trace in range(len(figure2["data"])):
    figure2_traces.append(figure2["data"][trace])

#Create a 1x2 subplot
this_figure = sp.make_subplots(rows=2, cols=1) 

# Get the Express fig broken down as traces and add the traces to the proper plot within in the subplot
for traces in figure1_traces:
    this_figure.append_trace(traces, row=1, col=1)
for traces in figure2_traces:
    this_figure.append_trace(traces, row=2, col=1)

#the subplot as shown in the above image
this_figure

In [ ]:
# fig = px.line(x = btc.date, y = MACD, title = 'BTC MACD vs Signal Line',
#               labels={
#                      "x": "Date",
#                      "y": ""
#                      })
# fig.add_scatter(x = btc.date, y = ema_btc_12, name = 'EMA(12)')
# fig.add_scatter(x = btc.date, y = ema_btc, name = 'EMA(26)')
# fig.add_scatter(x = btc.date, y = MACD, name = 'MACD')
# fig.add_scatter(x = btc.date, y = signal, name = 'Signal')
# fig.add_bar(x = btc.date, y = histogram, name = 'Histograma')


### Relative Strength Index

In [ ]:
btc_rsi = btc_ft[['date', 'close']]

In [ ]:
up = [0]
down = [0]
for i in range(1, len(btc_rsi)):
  x = btc_rsi.close.iloc[i]-btc_rsi.close.iloc[i-1]
  if x > 0:
    up.append(x)
    down.append(0)
  else:
    up.append(0)
    down.append(abs(x))

In [ ]:
btc_rsi = btc_rsi.assign(U = up, D = down)

In [ ]:
avgU = ema(btc_rsi.U, 14, 2)
avgD = ema(btc_rsi.D, 14, 2)

In [ ]:
btc_rsi = btc_rsi.assign(avgU = avgU, avgD = avgD)

In [ ]:
btc_rsi['RS'] = btc_rsi.avgU/btc_rsi.avgD
btc_rsi['RSI'] = 100 - 100/(1+btc_rsi.RS)
btc_rsi = btc_rsi.iloc[2:, :]

In [ ]:
fig = px.line(title = 'BTC MACD vs Signal Line')
figure1 = fig.add_scatter(x = btc_rsi['date'], y = btc_rsi['close'], name = 'Close Prices')

fig1 = px.line() 
fig1 = fig1.add_scatter(x = btc_rsi.date, y = MACD[2:], name = 'MACD')
fig1 = fig1.add_scatter(x = btc_rsi.date, y = signal[2:], name = 'Signal')
fig1 = fig1.add_bar(x = btc_rsi.date, y = histogram[2:], name = 'Histograma')

figure2 = fig1

fig2 = px.line()
figure3 = fig2.add_scatter(x = btc_rsi['date'], y = btc_rsi['RSI'], name = 'BTC RSI 14 days')

# For as many traces that exist per Express figure, get the traces from each plot and store them in an array.
# This is essentially breaking down the Express fig into it's traces
figure1_traces = []
figure2_traces = []
figure3_traces = []
for trace in range(len(figure1["data"])):
    figure1_traces.append(figure1["data"][trace])
for trace in range(len(figure2["data"])):
    figure2_traces.append(figure2["data"][trace])
for trace in range(len(figure3["data"])):
    figure3_traces.append(figure3["data"][trace])  

#Create a 1x2 subplot
this_figure = sp.make_subplots(rows=3, cols=1) 

# Get the Express fig broken down as traces and add the traces to the proper plot within in the subplot
for traces in figure1_traces:
    this_figure.append_trace(traces, row=1, col=1)
for traces in figure2_traces:
    this_figure.append_trace(traces, row=2, col=1)
for traces in figure3_traces:
    this_figure.append_trace(traces, row=3, col=1)

#the subplot as shown in the above image
this_figure

### Bollinger Bands

In [ ]:
def ma(ts, days):
  avg = np.zeros(len(ts))
  for i in range(days+1, len(ts)):
    avg[i] = np.sum(ts.iloc[(i-days):i])/days
  return avg

In [ ]:
btc_rsi['ma20'] = ma(btc_rsi.close, 20)

In [ ]:
# def msd(ts, n):
#   sd = np.zeros(len(ts))
#   for i in range(n, len(ts)):
#     sd[i] = np.std(ts[i-n:i])
#   return sd

In [ ]:
btc_rsi['upper_band'] = np.std(btc_rsi.close) + btc_rsi['close']
btc_rsi['lower_band'] =  + btc_rsi['close'] - np.std(btc_rsi.close)

In [ ]:
fig = px.line(title = 'BTC MACD vs Signal Line')
figure1 = fig.add_scatter(x = btc_rsi['date'], y = btc_rsi['close'], name = 'Close Prices')

fig1 = px.line() 
fig1 = fig1.add_scatter(x = btc_rsi.date, y = MACD[2:], name = 'MACD')
fig1 = fig1.add_scatter(x = btc_rsi.date, y = signal[2:], name = 'Signal')
fig1 = fig1.add_bar(x = btc_rsi.date, y = histogram[2:], name = 'Histograma')

figure2 = fig1

fig2 = px.line()
figure3 = fig2.add_scatter(x = btc_rsi['date'], y = btc_rsi['RSI'], name = 'BTC RSI 14 days')

fig4 = px.line() 
fig4 = fig4.add_scatter(x = btc_rsi.date, y = btc_rsi['upper_band'], name = 'BBU')
fig4 = fig4.add_scatter(x = btc_rsi.date, y = btc_rsi['lower_band'], name = 'BBL', fill='tonexty')
figure4 = fig4.add_scatter(x = btc_rsi.date, y = btc_rsi['ma20'], name = 'SMA(20)')

# For as many traces that exist per Express figure, get the traces from each plot and store them in an array.
# This is essentially breaking down the Express fig into it's traces
figure1_traces = []
figure2_traces = []
figure3_traces = []
figure4_traces = []
for trace in range(len(figure1["data"])):
    figure1_traces.append(figure1["data"][trace])
for trace in range(len(figure2["data"])):
    figure2_traces.append(figure2["data"][trace])
for trace in range(len(figure3["data"])):
    figure3_traces.append(figure3["data"][trace])  
for trace in range(len(figure4["data"])):
    figure4_traces.append(figure4["data"][trace])  

#Create a 1x2 subplot
this_figure = sp.make_subplots(rows=4, cols=1) 

# Get the Express fig broken down as traces and add the traces to the proper plot within in the subplot
for traces in figure1_traces:
    this_figure.append_trace(traces, row=1, col=1)
for traces in figure2_traces:
    this_figure.append_trace(traces, row=2, col=1)
for traces in figure3_traces:
    this_figure.append_trace(traces, row=3, col=1)
for traces in figure4_traces:
    this_figure.append_trace(traces, row=4, col=1)

#the subplot as shown in the above image
this_figure